In [ ]:
# In this notebook I plan on exploring the dataset afo

In [12]:
import os
import glob

In [9]:
# Mac local path
root_path =  r'/Users/krish/ljmu/1.data/afo/'
# result_root = root_path + '3.results/09112022-testing-code/'
# Path(result_root).mkdir(parents=True, exist_ok=True)

In [10]:
# Lets study the class distribution i.e number of figures with and without humans
images_with_humans = 0
images_no_humans = 0
for annotation in glob.glob(root_path+'1category_labels/*.txt'):
    with open(annotation,'r') as fp:
        number_of_human = len(fp.readlines())
    if number_of_human == 0:
        images_no_humans+=1
    else:
        images_with_humans+=1
    

In [11]:
print(images_no_humans,images_with_humans)
# Severe class imbalance, but dont forget tiling changes everything

729 2912


#### Lets tile and then study the same 

In [16]:
import pandas as pd
import numpy as np
from PIL import Image
from shapely.geometry import Polygon, Point
from matplotlib import pyplot as plt
import glob
from pathlib import Path

In [20]:
### Not sure what size should I tile to ..... The images are of better quality, so the objects are much smaller in size
# get all image names
imnames = glob.glob('/Users/krish/ljmu/1.data/afo/images/*.jpg')
#imnames = glob.glob('/content/drive/MyDrive/ljmu/1.data/swimmers_dataset/krish_train/*.jpg')
# specify path for a new tiled dataset
newpath = '/Users/krish/ljmu/1.data/afo/tiled/ts/'
#newpath = '/content/drive/MyDrive/ljmu/1.data/sampletiled/ts'
falsepath = '/Users/krish/ljmu/1.data/afo/tiled/false/'
#falsepath = '/content/drive/MyDrive/ljmu/1.data/sampletiled/false'
# python program to check if a path exists
#if path doesn’t exist we create a new path

#creating a new directory called pythondirectory
Path(newpath).mkdir(parents=True, exist_ok=True)
Path(falsepath).mkdir(parents=True, exist_ok=True)

# specify slice width=height
slice_size = 500

# tile all images in a loop

for imname in imnames:
    im = Image.open(imname)
    imr = np.array(im, dtype=np.uint8)
    height = imr.shape[0]
    width = imr.shape[1]
    labname = imname.split('/')[-1].replace('.jpg', '.txt')
    labels = pd.read_csv(root_path+'1category_labels/'+labname, sep=' ', names=['class', 'x1', 'y1', 'w', 'h'])
    
    # we need to rescale coordinates from 0-1 to real image height and width
    labels[['x1', 'w']] = labels[['x1', 'w']] * width
    labels[['y1', 'h']] = labels[['y1', 'h']] * height
    
    boxes = []
    #print(labels)
    # convert bounding boxes to shapely polygons. We need to invert Y and find polygon vertices from center points
    for row in labels.iterrows():
        x1 = row[1]['x1'] - row[1]['w']/2
        y1 = (height - row[1]['y1']) - row[1]['h']/2
        x2 = row[1]['x1'] + row[1]['w']/2
        y2 = (height - row[1]['y1']) + row[1]['h']/2

        boxes.append((int(row[1]['class']), Polygon([(x1, y1), (x2, y1), (x2, y2), (x1, y2)])))
    
    counter = 0
    print('Image:', imname)
    # create tiles and find intersection with bounding boxes for each tile
    for i in range((height // slice_size)):
        for j in range((width // slice_size)):
            x1 = j*slice_size
            y1 = height - (i*slice_size)
            x2 = ((j+1)*slice_size) - 1
            y2 = (height - (i+1)*slice_size) + 1

            pol = Polygon([(x1, y1), (x2, y1), (x2, y2), (x1, y2)])
            imsaved = False
            slice_labels = []

            for box in boxes:
                if pol.intersects(box[1]):
                    inter = pol.intersection(box[1])        
                    
                    if not imsaved:
                        sliced = imr[i*slice_size:(i+1)*slice_size, j*slice_size:(j+1)*slice_size]
                        sliced_im = Image.fromarray(sliced)
                        filename = imname.split('/')[-1]
                        ##filename = imname
                        slice_path = newpath + filename.replace('.jpg', f'_{i}_{j}.jpg')
                        
                        slice_labels_path = newpath + filename.replace('.jpg', f'_{i}_{j}.txt')
                        
                        print(slice_path)
                        #print('hi')
                        sliced_im.save(slice_path)
                        imsaved = True                    
                    
                    # get the smallest polygon (with sides parallel to the coordinate axes) that contains the intersection
                    new_box = inter.envelope 
                    
                    # get central point for the new bounding box 
                    centre = new_box.centroid
                    
                    # get coordinates of polygon vertices
                    x, y = new_box.exterior.coords.xy
                    
                    # get bounding box width and height normalized to slice size
                    new_width = (max(x) - min(x)) / slice_size
                    new_height = (max(y) - min(y)) / slice_size
                    
                    # we have to normalize central x and invert y for yolo format
                    new_x = (centre.coords.xy[0][0] - x1) / slice_size
                    new_y = (y1 - centre.coords.xy[1][0]) / slice_size
                    
                    counter += 1

                    slice_labels.append([box[0], new_x, new_y, new_width, new_height])
            
            # save txt with labels for the current tile
            if len(slice_labels) > 0:
                slice_df = pd.DataFrame(slice_labels, columns=['class', 'x1', 'y1', 'w', 'h'])
                #print(slice_df)
                slice_df.to_csv(slice_labels_path, sep=' ', index=False, header=False, float_format='%.6f')
            
            # if there are no bounding boxes intersect current tile, save this tile to a separate folder 
            if not imsaved:
                sliced = imr[i*slice_size:(i+1)*slice_size, j*slice_size:(j+1)*slice_size]
                sliced_im = Image.fromarray(sliced)
                filename = imname.split('/')[-1]
                #filename = imname
                slice_path = falsepath + filename.replace('.jpg', f'_{i}_{j}.jpg')                

                sliced_im.save(slice_path)
                print('Slice without boxes saved')
                imsaved = True
#     if counter == 100:
#         break

Image: /Users/krish/ljmu/1.data/afo/images/b1_37.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_37_0_0.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_37_1_1.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_37_1_2.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_37_1_3.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_37_1_4.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_37_2_1.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_37_2_2.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_37_2_3.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_37_2_4.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_37_3_1.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_37_3_2.jpg
Slice without boxes saved
/Users/kris

Image: /Users/krish/ljmu/1.data/afo/images/b1_239.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_239_1_2.jpg
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_239_1_4.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_239_1_5.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_239_2_2.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_239_2_3.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_239_2_4.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_239_2_5.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_239_3_2.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_239_3_3.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_239_3_4.jpg


/Users/krish/ljmu/1.data/afo/tiled/ts/b1_211_1_3.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_211_2_0.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_211_2_1.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_211_2_2.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_211_2_3.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_211_3_1.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_211_3_2.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_211_3_3.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Image: /Users/krish/ljmu/1.data/afo/images/f_81.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_81_0_0.jpg
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/f_81_0_3.jpg
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/f_81_0_5.jpg
/Users/krish/ljmu/1.data/afo/tile

Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_0_5.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_0_6.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_1_0.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_1_1.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_1_2.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_1_3.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_1_4.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_1_5.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_1_6.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_2_0.jpg
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_2_2.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_2_3.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_2_4.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_2_5.jpg
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_3_0.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_3_1.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_122_3_2.jpg
/Users/krish

Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/w2_100_2_0.jpg
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/w2_100_2_3.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/w2_100_3_0.jpg
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/w2_100_3_2.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/w2_100_3_3.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/w2_100_3_4.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/w2_100_3_5.jpg
Slice without boxes saved
Image: /Users/krish/ljmu/1.data/afo/images/s5_67.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Image: /Users/krish/ljmu/1.data/afo/images/s1_234.jpg
Slice without boxes saved
Slice without boxes saved
Sl

...

Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/a_351_3_3.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/a_351_3_4.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/a_351_3_5.jpg
Slice without boxes saved
Image: /Users/krish/ljmu/1.data/afo/images/s5_42.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Image: /Users/krish/ljmu/1.data/afo/images/s1_211.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Image: /Users/krish/ljmu/1.data/afo/images/a_345.jpg
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/a_345_0_1.jpg
/Users/krish/ljmu/1.data/afo/tiled

/Users/krish/ljmu/1.data/afo/tiled/ts/f_113_2_6.jpg
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/f_113_3_1.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_113_3_2.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_113_3_3.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_113_3_4.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_113_3_5.jpg
Slice without boxes saved
Image: /Users/krish/ljmu/1.data/afo/images/s5_81.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Image: /Users/krish/ljmu/1.data/afo/images/s2_311.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/s2_311_1_0.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/k

/Users/krish/ljmu/1.data/afo/tiled/ts/f_98_3_3.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_98_3_4.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/f_98_3_5.jpg
Slice without boxes saved
Image: /Users/krish/ljmu/1.data/afo/images/b1_208.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_208_1_2.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_208_1_3.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_208_2_1.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_208_2_2.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_208_2_3.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/b1_208_3_1.jpg
/Users/

/Users/krish/ljmu/1.data/afo/tiled/ts/a_1147_2_5.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/a_1147_2_6.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/a_1147_3_3.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/a_1147_3_4.jpg
Slice without boxes saved
Slice without boxes saved
Image: /Users/krish/ljmu/1.data/afo/images/s1_32.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Image: /Users/krish/ljmu/1.data/afo/images/a_147.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
Slice 

/Users/krish/ljmu/1.data/afo/tiled/ts/a_1184_2_4.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/a_1184_2_5.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/a_1184_2_6.jpg
Slice without boxes saved
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/a_1184_3_3.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/a_1184_3_4.jpg
Slice without boxes saved
Slice without boxes saved
Image: /Users/krish/ljmu/1.data/afo/images/i1_8.jpg
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/i1_8_0_2.jpg
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/i1_8_0_4.jpg
Slice without boxes saved
Slice without boxes saved
/Users/krish/ljmu/1.data/afo/tiled/ts/i1_8_1_2.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/i1_8_1_3.jpg
/Users/krish/ljmu/1.data/afo/tiled/ts/i1_8_1_4.jpg


In [21]:
# Think before running the tiler. took a hell lot of time
# Lets see the distribution now

In [6]:
import pandas as pd
import glob

In [12]:
df_true = pd.DataFrame(columns = ['name','humans','number_of_humans'])
df_false = pd.DataFrame(columns = ['name','humans','number_of_humans'])


for images_path in glob.glob(root_path+'tiled/ts/*.jpg'):
    label_path = images_path.replace('.jpg','.txt')
    
    with open(label_path,'r') as fp:
        number_of_human = len(fp.readlines())
    df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
    

df_false['name'] = glob.glob(root_path+'tiled/false/*.jpg')
df_false.humans = 0
df_false.number_of_humans = 0

df = df_true.append(df_false)

/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/

/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/

/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/

/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/

/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/

...

/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/

/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/

/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/

/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_true = df_true.append({'name':images_path,'humans':1,'number_of_humans':number_of_human},ignore_index=True)
/var/folders/

/var/folders/zk/p2gyqg915639vx6xr9xbs9cm0000gn/T/ipykernel_11975/3216234623.py:17: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df_true.append(df_false)


In [13]:
df

name humans  \
0      /Users/krish/ljmu/1.data/afo/tiled/ts/a_1178_1...      1   
1      /Users/krish/ljmu/1.data/afo/tiled/ts/k4_184_0...      1   
2      /Users/krish/ljmu/1.data/afo/tiled/ts/b1_211_2...      1   
3      /Users/krish/ljmu/1.data/afo/tiled/ts/r4_109_1...      1   
4      /Users/krish/ljmu/1.data/afo/tiled/ts/e_47_2_3...      1   
...                                                  ...    ...   
44445  /Users/krish/ljmu/1.data/afo/tiled/false/a_357...      0   
44446  /Users/krish/ljmu/1.data/afo/tiled/false/w1_29...      0   
44447  /Users/krish/ljmu/1.data/afo/tiled/false/a_106...      0   
44448  /Users/krish/ljmu/1.data/afo/tiled/false/b1_16...      0   
44449  /Users/krish/ljmu/1.data/afo/tiled/false/z3_54...      0   

      number_of_humans  
0                    3  
1                    1  
2                    1  
3                    3  
4                    3  
...                ...  
44445                0  
44446                0  
44447                0  
44448                0  
44449                0  

[62403 rows x 3 columns]

In [14]:
print(df_true.shape,df_false.shape)

(17953, 3) (44450, 3)


In [49]:
df_true

name humans  \
0      /Users/krish/ljmu/1.data/afo/tiled/ts/a_1178_1...      1   
1      /Users/krish/ljmu/1.data/afo/tiled/ts/k4_184_0...      1   
2      /Users/krish/ljmu/1.data/afo/tiled/ts/b1_211_2...      1   
3      /Users/krish/ljmu/1.data/afo/tiled/ts/r4_109_1...      1   
4      /Users/krish/ljmu/1.data/afo/tiled/ts/e_47_2_3...      1   
...                                                  ...    ...   
17948  /Users/krish/ljmu/1.data/afo/tiled/ts/k5_45_1_...      1   
17949  /Users/krish/ljmu/1.data/afo/tiled/ts/i3_153_0...      1   
17950  /Users/krish/ljmu/1.data/afo/tiled/ts/s5_252_1...      1   
17951  /Users/krish/ljmu/1.data/afo/tiled/ts/r2_85_2_...      1   
17952  /Users/krish/ljmu/1.data/afo/tiled/ts/e_99_0_1...      1   

      number_of_humans  
0                    3  
1                    1  
2                    1  
3                    3  
4                    3  
...                ...  
17948                1  
17949                2  
17950                1  
17951                2  
17952                3  

[17953 rows x 3 columns]

# Update 15112022
Adding code to divide bring in train and test forders or a fixed csv defining whats test train and validation.
I think the later is better, as I have already extensively used this oflder hierarchy.


In [24]:
from sklearn.model_selection import train_test_split


In [25]:
train_df, test_df = train_test_split(df, 
                                   test_size = 0.25, 
                                   random_state = 1998,
                                   shuffle = df['humans']) # Stratify makes sure that the distribution is maintained.

In [26]:
train_df.to_csv(root_path+'tiled/afo_train_df.csv')

In [27]:
test_df.to_csv(root_path+'tiled/afo_test_df.csv')

In [28]:
train_df.humans.sum()/train_df.shape[0]

0.2877013802828939

In [29]:
test_df.humans.sum()/valid_df.shape[0]

0.28767386705980386

In [ ]:
# From here on use this csv for the generator.